# Calibrating data

In this tutorial chapter you will process data for the first time. We take the example of reducing raw science frames. This involves trimming, de-biasing, flat-fielding, illumination-correction, as well as the detection of saturated pixels, cosmic-rays and satellite tracks. Together with cold- and hot pixels these affected pixels are assigned a weight of zero in the weight map, which is also created. The results will be stored on the Astro-WISE dataservers and database.

### Database projects and privileges

Data in the database is organized in projects. To see in which project you are currently working:

In [ ]:
print(context.get_current_project())

For example the output could be:

   Project:     OMEGACAM@VST  (id = 36)  
   Description: All public data for OmegaCAM.  OmegaCAM is a 1 square  
                degree wide field, optical, 16k X 16k pixel camera for the VLT Survey  
                Telescope (VST) on Paranal Observatory.  
   Instrument:  OMEGACAM  
   Maximum Privileges: 4 (World)  
   Current Privileges: 1 (MyDB)  

If you are doing this tutorial as part of a course you should produce the data in a certain project: *TUTORIAL*. Select this project by typing:

In [ ]:
context.set_project('TUTORIAL')

If you have not been asked to enter a certain project you can use the project you are in now. From now on, everything you create will be stored inside the chosen project. There will be other members of this project. You can set privileges to restrict who can view and access data within a project. A privilege of 1 means only you can view and access the data:

In [ ]:
context.set_privileges(1)

From here on, everything you create will be stored at privilege level 1 in the chosen project: only you can view/access the data. To allow other people in the project to see products, set privileges to 2 before you create them.

### Processing science frames

Selecting and exploring RawScienceFrames Enter the following query that selects the raw science data objects, i.e., instantiations of the class RawScienceFrame, from the database.

In [ ]:
query = (RawScienceFrame.instrument.name == 'OMEGACAM') & \
        (RawScienceFrame.template.start == datetime.datetime(2012, 6, 1, 8, 51, 44)) & \
        (RawScienceFrame.is_valid > 0)

To see how many raw science frames are found type:

In [ ]:
len(query)

These are 5 OmegaCAM exposures, each consisting of 32 CCDs (32 RawScienceFrames are created for a single exposure).
We select only the data of CCD #65 for now:

In [ ]:
query = query & (RawScienceFrame.chip.name == 'ESO_CCD_#65')
len(query)

To print the meta-data of the last RawScienceFrame use the ``info()`` method:

In [ ]:
raw = query.max('DATE_OBS')
raw.info()

To print only the observation dates, filter names, and maximum pixel value in the frame for all of them:

In [ ]:
for r in query: print(r.DATE_OBS, r.filter.name, r.imstat.max)

Download the FITS file of the frame we selected above:

In [ ]:
raw.retrieve()

Now that you have the file locally you can display it using your favorite image viewer.
To visually inspect a frame with the help of a few analysis tools type:

In [ ]:
raw.inspect()

*Note: the following does not work in Jupyter notebook*

This brings up a graphical window. Hover your mouse over an object in the window and hit 'w': this shows a 3D wire-frame plot of the pixel values around the mouse pointer. Hit 'q' when you hover over it to close the graphical window. For a listing of all hot-keys type:

<pre>help(raw.inspect)</pre>

<pre>
Help on method inspect in module astro.main.BaseFrame:

inspect(pixels=None, zone=None, kappa=3.0, iterations=2, cmap=None, vmin=None, vmax=None, interpolation='lanczos', width=6, ratio=None, viewer='skycat', force_figure=False, force_viewer=False, subplot_size=50, contour_levels=20, num_bins=100, extension=None, compare=False, level=0, other=None, clip=False, color=False) method of astro.main.RawFrame.RawScienceFrame instance
    Optional visual inspection for quality control displays image in a
    PyLab (MatPlotLib) window or optionally in an external viewer.
    
            pixels: optional list or array representing the image to be
                    inspected (can be MxN for greyscale, or MxNx3 for RGB)
              zone: tuple of (x0, y0, x1, y1) representing the image
                    coordinates of the two oposing corners of the sub
                    image to consider
             kappa: the factor by which the dynamic range is increased in
                    units of sigma (0 gives full range)
        iterations: number of iterations in the kappa-sigma range clipping
              cmap: PyLab color map instance
              vmin: lower display range in native units (e.g. ADU)
              vmax: upper display range in native units (e.g. ADU)
     interpolation: type of interpolation the PyLab viewer uses (nearest,
                    bilinear, etc.)
             width: width of the PyLab figure window (in inches)
             ratio: ratio by which to scale the figure height (default:
                    x_dim/y_dim)
            viewer: external viewer to use in case the image is too large
      force_figure: always use the PyLab figure window (Be Careful!
                    Statistics calculations on large images can be very
                    time and memory consuming.)
      force_viewer: always use the viewer
      subplot_size: width and height in pixels of region of interest
    contour_levels: number of contour levels for the contour plot of the
                    region of interest
          num_bins: number of bins in the histogram plot
         extension: extension of the filetype to save plot to (png, ps,
                    or eps) None disables saving
           compare: compare this frame to its previous version using
                    difference imaging (current-previous), pixels is
                    ignored
             level: depth of query for previous version (0 goes as deep
                    as possible) when compare is True
             other: a second of the same type of Frame object to replace
                    previous when compare is True (if color is True,
                    other can be a list of two images)
              clip: kappa-sigma clip each image prior to subtraction when
                    compare is True
             color: use color combining (RGB) instead of differencing
                    when compare is True (kappa, vmin/vmax only honored
                    when clip is True), this image is R, other is B if
                    single, other is [G, B] if it is a list
                    (EXPERIMENTAL)
    
    When force_viewer is False, inspect() displays basic image
    statistics (mean, stddev) and then a representation of the image
    that can be zoomed and panned.  Pressing various keys will give
    different results described below in a region of interest described
    by subplot_size:
    
          q - closes the most recent plot window when pressed in the
              main window
    [space] - displays the X and Y coordinate (FITS standard unit
              indexed) and the count level
          a - performs aperture photometry on brightest feature in the
              region of interest (NOT YET IMPLEMENTED)
          c - displays a contour plot of the region of interest (see
              contour_levels)
          h - displays a histogram of the pixel values of the region of
              interest (see num_bins)
          r - displays a radial plot of the brightest feature in the
              region of interest
          w - displays a wireframe plot of the region of interest
          p - displays profile plots in both X and Y dimensions versus
              intensity (count level)

    NOTE: None of the commands above work in the subplots.
</pre>

*Proceed here (both awe and jupyter)*


Reduce the RawScienceFrames that you found above.
See [this HOW-TO](http://doc.astro-wise.org/man_howto_calibrationpipelines.html) for an overview of how to process data in Astro-WISE. You will use standard recipes to reduce the RawScienceFrames. It is straightforward to adapt these or to write your own recipes, but this is beyond the scope of this tutorial.

In the Astro-WISE environment you may choose the compute cluster (the ``Distributed Processing Unit`` or ``DPU``) where the data reduction processes run. In that case no results are stored on your local machine. Created data (FITS files) are stored on the dataserver while meta-data is committed to the database.

To de-bias and flatfield the above raw science data using the DPU you can use the``Reduce`` recipe:

In [ ]:
filenames = [raw.filename for raw in query]
dpu.run('Reduce', instrument='OMEGACAM', raw_filenames=filenames,
             commit=True)

The ``commit=True`` switch ensures that your data is committed. Choosing ``commit=False`` (or omitting the option, as below) will perform a "dry run": everything will be done except committing your results at the end.

By specifying the template start date, you can do the query and reduction at once:

In [ ]:
dpu.run('Reduce', instrument='OMEGACAM', template='2012-06-01T08:51:44',
        chip='ESO_CCD_#65')

You can view the status of your DPU job via

In [ ]:
dpu.get_status()

or by browsing the DPU server's webpage. See the links found on the [Processing Grid page page](http://www.astro-wise.org/portal/aw_prompt.shtml) (in particular the [DPU Groningen](https://dpu.hpc.rug.astro-wise.org/)).
You can see how the processing went by retrieving the processing logs from the DPU.

In [ ]:
dpu.get_logs()

This command will not return anything until the process has been completed. The returned lines are also written to a single ("date+time".log) file in your local directory per awe-prompt session.
To cancel DPU processing jobs use the ``cancel_job()`` method:

In [ ]:
for jobid in dpu.get_jobids(): dpu.cancel_job(jobid)

While it is faster to calibrate RawScienceFrames in parallel on a DPU it can sometimes be convenient to use your local machine. In this case the results are left in your current working directory. To de-bias and flatfield your raw science data found above using using local CPU you can use the same Reduce recipe as follows:

In [ ]:
task = ReduceTask(instrument='OMEGACAM', raw_filenames=filenames, commit=True)
task.execute()

or...

In [ ]:
task = ReduceTask(instrument='OMEGACAM', template='2012-06-01T08:51:44', chip='ESO_CCD_#65', commit=True)
task.execute()

### Inspect the results: ReducedScienceFrame

The results of the above process are de-biased, flatfielded science frames, called ``ReducedScienceFrames``. To select one of the ones you just created type:

In [ ]:
qred = (ReducedScienceFrame.raw == raw)
red = qred.project_only().user_only().max('creation_date')

The first command queries for all ReducedScienceFrames which were created from the RawScienceFrame object query[0] in all projects you have access to. The second command narrows the selected ReducedScienceFrames to only those created within the project you are currently in. The third command zooms in on the subset of those that were created by you. The last command selects the ReducedScienceFrame that you created most recently. To do all this in a single command for all RawScienceFrames in query:

In [ ]:
qred = [(ReducedScienceFrame.raw==raw).project_only().user_only().max('creation_date') for raw in query]

Inspect the ReducedScienceFrame like you did earlier:

In [ ]:
red.inspect()

Determine which calibration frames were used. As you did not create the bias frames and flatfields, the Astro-WISE environment selected those for you. To get general information on which ones were used:

In [ ]:
red.bias.info()
red.flat.info()

and to inspect one of the RawBiasFrames that were used to create the bias frame:

In [ ]:
red.bias.raw_bias_frames[0].inspect()

We have not configured anything beyond specifying the input frames in the previous examples. Find out which other parameters can be configured. 

See the [configuration HOW-TO](http://doc.astro-wise.org/man_howto_configure.html) for more details. Calling the ``help()`` function on the Task gives a description of its possible arguments. These are mostly query parameters which determine which input frames (RawScienceFrames in this case) will be reduced. In addition an argument ``pars`` can be specified which contains the processing parameters.

help(ReduceTask)

<pre>
Help on class ReduceTask in module astro.recipes.Reduce:

class ReduceTask(astro.recipes.mods.Task.Task, astro.recipes.mods.Task.ImagePipe
lineMixin)
 |  --------------------------------------------------------------------------
 |  
 |     CATEGORY : data processing, image pipeline.
 |  
 |     PURPOSE  : making reduced science frames (flat-fielded, de-biased)
 |  
 |  --------------------------------------------------------------------------
 |  
 |     This task is used to create ReducedScienceFrame's.
 |  
 |     The task must be instantiated with the appropriate keyword arguments
 |     described below, and is executed using its 'execute' method.
 |  
 |  --------------------------------------------------------------------------
 |  
 |     Example 1 of use from the awe prompt:
 |  
 |       awe> task = ReduceTask(instrument='OMEGACAM', chip='ESO_CCD_#65',
 |                              filter='OCAM_i_SDSS', date='2015-03-01',
 |                              object='KIDS_186.5_-2.5')
 |       awe> task.execute()
 |  
 |     Example 2 of use from the awe prompt:
 |  
 |       awe> task = ReduceTask(instrument='WFI',
 |                              raw_filenames=['wfi60757_1.fits'])
 |       awe> task.execute()
 |  
 |  
 |     See the section below for an overview of the possible constructor
 |     keywords.
 |  
 |  --------------------------------------------------------------------------
 |  
 |     Two sets of query keywords can be provided in the constructor of the
 |     task:
 |  
 |         1) one list of filenames.
 |         2) a set of global query parameters (like date, filter and chip).
 |  
 |     The first of these sets has precedence over the second.
 |  
 |     The first set of possible keywords is one list of filenames:
 |  
 |        raw_filenames (filenames of the raw science frames, list of strings)
 |  
 |     The second set of possible keywords is:
 |  
 |        date        (string)
 |        instrument  (string)
 |        chip        (string)
 |        filter      (string)
 |        template    (string)
 |        object      (string or using wildcards like M33_?_?, M33_V*)
 |  
 |     Finally, the following parameters can also be set in the constructor:
 |  
 |        force_defringe (integer 0 or 1. Default 0. Use this only for example
 |                        for WFI R filter, which is not automatically
 |                        defringed)
 |        ofieldedverscan       (integer 0-13. Default 6)
 |        pars           (dictionary of configuration parameters, example:
 |           {'ReducedScienceFrame.process_params.FRINGE_THRESHOLD_HIGH': 6.0})
 |        commit         (boolean: False or True. Default False)
 |  
 |     For all the keywords documented here, the type of the values assigned
 |     to it is given between parentheses.
 |  
 |  --------------------------------------------------------------------------
 |  
 |  Method resolution order:
 |      ReduceTask
 |      astro.recipes.mods.Task.Task
 |      common.util.Pipeline.Task
 |      astro.recipes.mods.Task.TaskMixin
 |      astro.recipes.mods.Task.ImagePipelineMixin
 |      builtins.object
 |  
 |  Methods defined here:
 |  
 |  __init__(self, *args, **kwargs)
 |      Recognized options for the astro.recipes.Reduce OptionsParser are:
 |      "i" or "instrument" (default: )
 |      "f" or "filter" (default: )
 |      "c" or "chip" (default: )
 |      "d" or "date" (default: )
 |      "o" or "object" (default: )
 |      "tpl" or "template" (default: None)
 |      "oc" or "overscan" (default: 6)
 |      "rfd" or "rfd_filenames" (default: [])
 |      "raw" or "raw_filenames" (default: [])
 |      "e" or "exptime" (default: -1)
 |      "fd" or "force_defringe" (default: 0)
 |      "p" or "pars" (default: {})
 |      "C" or "commit" (default: False)
etc.
</pre>

Instantiate the Pars class with as argument the task, the pipeline identifier used in the dpu call or the class:

In [ ]:
p = Pars(ReduceTask, instrument='OMEGACAM')
p = Pars('Reduce', instrument='OMEGACAM')
p = Pars(ReducedScienceFrame, instrument='OMEGACAM')

By setting the instrument argument, instrument specific default processing parameters are used. Now call the ``show()`` method:

In [ ]:
p.show()

A parameter can be set as follows (use Tab completion):

In [ ]:
p.ReducedScienceFrame.process_params.FRINGE_THRESHOLD_HIGH = 6.0

Call the get() method to obtain the dictionary that you can supply to the task:

In [ ]:
p.get()